# Mixed Effects / Heirarchical Modelling 

Mixed Effect (also nkown as heirarchical) models may be applicable when the data is nested or you have repeat observations for a given unit. Examples include user level data where treatment occured at the geographic level, student performance where the intervention was at the class level, patient outcomes where treatments were assigned by doctor etc.

In [1]:
import numpy as np
import pandas as pd 
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px 
import plotly.graph_objects as go
import statsmodels.api as sm
import statsmodels.formula.api as smf
import scipy

sns.set_theme(context = 'notebook', style = 'whitegrid')

## College student performance given different teaching methods Example
In this example we are interested in learning the effect of different teaching methods on student performance here represented by the variable 'score'. A nested data structure is created by randomly assigning all students to one instructor and each instructor to one teaching method. The data is generated such that student performance is affected by their hgh school gpa, their instrcutor as well as the teaching method the instrcutor used (independent of the instrccutor effect). 
  

In [100]:

num_student = 50000
num_instructor = 50
num_method = 5

all_students = np.arange(0, num_student, step =1)
all_instructors = np.arange(0, num_instructor, step = 1)
all_methods = np.arange(0, num_method, 1)

students_per_instructor = int(num_student/num_instructor)
instructors_per_method = int(num_instructor/num_method)

### 1) Assign students to an instrcutor
student_assignment = []

for i in all_instructors:
    # randomly assign the appropriate number of students to an instructor 
    assigned_students = np.random.choice(all_students, size = students_per_instructor, replace = False)
    instructor = np.repeat(i, repeats = students_per_instructor)
    assignment = np.column_stack((assigned_students, instructor)).tolist()
    # remove students from the pool that have already been assigned
    all_students = np.setdiff1d(all_students, assigned_students)
    # extend() avoids nested list issues for simple df creation (in lieu of append())
    student_assignment.extend(assignment)

df1 = pd.DataFrame(student_assignment, columns=['student','instructor']).sort_values(by = 'student').reset_index(drop = True)

### 2) Assign instructors to a method
instructor_assignment = []

for i in all_methods:
    # randomly assign the appropriate number of students to an instructor 
    assigned_instructors = np.random.choice(all_instructors, size = instructors_per_method, replace = False)
    method = np.repeat(i, repeats = instructors_per_method)
    assignment = np.column_stack((assigned_instructors, method)).tolist()
    # remove students from the pool that have already been assigned
    all_instructors = np.setdiff1d(all_instructors, assigned_instructors)
    # extend() avoids nested list issues for simple df creation (in lieu of append())
    instructor_assignment.extend(assignment)

df2 = pd.DataFrame(instructor_assignment, columns=['instructor','method']).sort_values(by = 'instructor').reset_index(drop = True)

df = df1.merge(df2, on = 'instructor', how = 'left')


### 3) Generating the dependant variable and effects of instrcutor/method
instructor_effect = pd.Series(np.random.normal(loc= 1, scale = .1, size = num_instructor), name = 'instructor_effect')
method_effect = pd.Series(np.random.normal(loc= 1, scale = .1, size = num_method), name = 'method_effect')
method_effect.loc[0] = 1

print("typical instructor effect (in absolute terms)", ((instructor_effect -1).abs().mean())*100, "%")
print("typical method effect (in absolute terms)", ((method_effect -1).abs().mean())*100, "%")
print('------------------------------')
print((method_effect -1)*100, "%")

# Adding in a continuous variable: high school gpa
df['hs_gpa'] = np.random.normal(loc = 3,scale = .25, size = num_student)
df.loc[df['hs_gpa'] > 4] == 4



df = df.merge(instructor_effect, left_on='instructor', right_index=True, how = 'left')
df = df.merge(method_effect, left_on='method', right_index=True, how = 'left')

hs_gpa_slope = 19
hs_gpa_intercept = 15
df['score'] = (hs_gpa_intercept + hs_gpa_slope*df['hs_gpa'])*df.instructor_effect*df.method_effect + np.random.normal(loc = 0, scale = 10, size = num_student)
df.loc[df['score'] >= 100, 'score'] = 100

#df = df.astype({'student':'object','instructor':'object','method':'object'})

display(df.head())



typical instructor effect (in absolute terms) 8.122727916594409 %
typical method effect (in absolute terms) 7.157714071374914 %
------------------------------
0     0.000000
1   -11.472786
2     3.122577
3    -3.306792
4    17.886415
Name: method_effect, dtype: float64 %


student  instructor  method    hs_gpa  instructor_effect  method_effect  \
0        0          31       2  3.127517           1.094165       1.031226   
1        1          49       2  2.571498           1.042213       1.031226   
2        2           9       3  2.697218           1.045718       0.966932   
3        3          41       3  3.208782           1.110705       0.966932   
4        4          18       0  3.015154           0.910004       1.000000   

       score  
0  84.988184  
1  60.311044  
2  57.319158  
3  68.540865  
4  47.439076

### Exploratory Data Analysis Plots

In [101]:
fig  = px.imshow(df.corr(), 
                text_auto=True,
                title = 'Correlation Matrix for Call Center Data')
fig.update_layout(height = 500, width = 1000) 
fig.show()
df.corr()

student  instructor    method    hs_gpa  \
student            1.000000   -0.002133  0.000689  0.001537   
instructor        -0.002133    1.000000  0.174439 -0.005045   
method             0.000689    0.174439  1.000000 -0.008962   
hs_gpa             0.001537   -0.005045 -0.008962  1.000000   
instructor_effect -0.007003   -0.027447 -0.219438  0.005233   
method_effect      0.001234   -0.110589  0.644716 -0.004198   
score             -0.004709   -0.072383  0.185321  0.345067   

                   instructor_effect  method_effect     score  
student                    -0.007003       0.001234 -0.004709  
instructor                 -0.027447      -0.110589 -0.072383  
method                     -0.219438       0.644716  0.185321  
hs_gpa                      0.005233      -0.004198  0.345067  
instructor_effect           1.000000      -0.250081  0.393895  
method_effect              -0.250081       1.000000  0.347485  
score                       0.393895       0.347485  1.000000

In [91]:

fig = px.histogram(df, 
                x = 'score', 
                color = 'method', 
                marginal= 'box', 
                opacity = .5, 
                title = 'Histogram of Scores by Teaching Method')
fig.update_layout(height = 500, 
                width = 1000, 
                barmode = 'overlay')
fig.show()

In [92]:
fig = px.scatter(df, 
                x = 'hs_gpa', 
                y = 'score', 
                color = 'method',
                opacity = .5,
                title = "Relationship between High School GPA and Score")
fig.update_layout(height = 500, 
                width = 1000)
fig.show()

### Running Heirarchical models in Statsmodels
Here we start by creating an OLS model that would be appropriate for this data but will see that there are strong multicollinearty issues. We then run the appropriate mixed model, grouping on instructor and see if we get similar warnings. Finally we will compare the result sof the mixed model to the actual effects to assess performance in this simulated data example.

In [105]:
model = smf.ols(formula='score ~ hs_gpa + C(instructor) + C(method)', data=df)
ols_results = model.fit()
ols_results.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                  score   R-squared:                       0.488
Model:                            OLS   Adj. R-squared:                  0.488
Method:                 Least Squares   F-statistic:                     953.3
Date:                Thu, 27 Oct 2022   Prob (F-statistic):               0.00
Time:                        21:32:35   Log-Likelihood:            -1.8494e+05
No. Observations:               50000   AIC:                         3.700e+05
Df Residuals:                   49949   BIC:                         3.704e+05
Df Model:                          50                                         
Covariance Type:            nonrobust                                         
=======================================================================================
                          coef    std err          t      P>|t|      [0.025      0.975]
---------------------------------------------------------------------------------------
Intercept              15.8283      0.496     31.937      0.000      14.857      16.800
C(instructor)[T.1]     -5.4871      0.437    -12.545      0.000      -6.344      -4.630
C(instructor)[T.2]      4.0991      0.294     13.958      0.000       3.523       4.675
C(instructor)[T.3]      4.9147      0.294     16.737      0.000       4.339       5.490
C(instructor)[T.4]     -0.4751      0.298     -1.594      0.111      -1.059       0.109
C(instructor)[T.5]     -0.0512      0.298     -0.172      0.864      -0.636       0.533
C(instructor)[T.6]      3.5462      0.437      8.107      0.000       2.689       4.404
C(instructor)[T.7]      4.8936      0.298     16.397      0.000       4.309       5.479
C(instructor)[T.8]     17.0409      0.298     57.174      0.000      16.457      17.625
C(instructor)[T.9]      1.9612      0.294      6.679      0.000       1.386       2.537
C(instructor)[T.10]    -8.2210      0.294    -27.998      0.000      -8.796      -7.645
C(instructor)[T.11]     0.3312      0.294      1.128      0.259      -0.244       0.907
C(instructor)[T.12]    -1.6982      0.437     -3.882      0.000      -2.556      -0.841
C(instructor)[T.13]    -8.7554      0.294    -29.819      0.000      -9.331      -8.180
C(instructor)[T.14]    -2.6854      0.298     -9.009      0.000      -3.270      -2.101
C(instructor)[T.15]   -10.2674      0.294    -34.965      0.000     -10.843      -9.692
C(instructor)[T.16]   -15.4317      0.437    -35.279      0.000     -16.289     -14.574
C(instructor)[T.17]     4.9051      0.298     16.449      0.000       4.321       5.490
C(instructor)[T.18]    -7.2385      0.298    -24.276      0.000      -7.823      -6.654
C(instructor)[T.19]    -7.1211      0.294    -24.252      0.000      -7.697      -6.546
C(instructor)[T.20]     8.1676      0.294     27.816      0.000       7.592       8.743
C(instructor)[T.21]     1.2477      0.294      4.249      0.000       0.672       1.823
C(instructor)[T.22]     1.8000      0.294      6.131      0.000       1.225       2.376
C(instructor)[T.23]    -0.7153      0.298     -2.398      0.017      -1.300      -0.131
C(instructor)[T.24]     7.5849      0.294     25.832      0.000       7.009       8.160
C(instructor)[T.25]     0.7614      0.294      2.593      0.010       0.186       1.337
C(instructor)[T.26]     2.0289      0.294      6.910      0.000       1.453       2.604
C(instructor)[T.27]   -14.7497      0.298    -49.473      0.000     -15.334     -14.165
C(instructor)[T.28]     6.9469      0.294     23.659      0.000       6.371       7.522
C(instructor)[T.29]     5.6188      0.294     19.136      0.000       5.043       6.194
C(instructor)[T.30]    -0.9481      0.294     -3.228      0.001      -1.524      -0.372
C(instructor)[T.31]    -0.5350      0.437     -1.223      0.221      -1.392       0.322
C(i

In [103]:
mixed = smf.mixedlm("score ~ hs_gpa + C(method)", data = df,  groups = df['instructor'])
results = mixed.fit()
results.summary()

<class 'statsmodels.iolib.summary2.Summary'>
"""
           Mixed Linear Model Regression Results
===========================================================
Model:             MixedLM Dependent Variable: score       
No. Observations:  50000   Method:             REML        
No. Groups:        50      Scale:              95.6649     
Min. group size:   1000    Log-Likelihood:     -185112.3943
Max. group size:   1000    Converged:          Yes         
Mean group size:   1000.0                                  
-----------------------------------------------------------
               Coef.  Std.Err.    z    P>|z|  [0.025 0.975]
-----------------------------------------------------------
Intercept      16.615    2.226   7.465 0.000  12.253 20.978
C(method)[T.1] -7.489    3.058  -2.449 0.014 -13.483 -1.495
C(method)[T.2]  5.109    3.058   1.670 0.095  -0.885 11.103
C(method)[T.3] -2.780    3.058  -0.909 0.363  -8.774  3.214
C(method)[T.4]  6.749    3.058   2.207 0.027   0.755 12.743
hs_gpa         18.800    0.175 107.429 0.000  18.457 19.143
Group Var      46.668    1.011                             
===========================================================

"""

How well does the heirarchical model capture the effects in the data?

In [107]:
print("Mixed MOdel Results")
print(results.params)
print("--------------------")
print("Actual Effects")
print("method effects: ", (method_effect -1)*100)

print("hs_gpa slope param: ", hs_gpa_slope)

Mixed MOdel Results
Intercept         16.615462
C(method)[T.1]    -7.488717
C(method)[T.2]     5.108634
C(method)[T.3]    -2.780447
C(method)[T.4]     6.749039
hs_gpa            18.800046
Group Var          0.487833
dtype: float64
--------------------
Actual Effects
method effects:  0     0.000000
1   -11.472786
2     3.122577
3    -3.306792
4    17.886415
Name: method_effect, dtype: float64
hs_gpa slope param:  19


## Florent Buisson O'rielly Book Example
In this data each row represents a call to a customer service representative. Each representative belongs to exactly one call center. In this example we are interested in knowing the determinants of the call CSAT which ranges from 0-10 and is a measure of customer satisfaction

In [47]:
call_df = pd.read_csv("https://raw.githubusercontent.com/FlorentBuissonOReilly/BehavioralDataAnalysis/master/Chapter%2010%20-%20Cluster%20Randomization%20and%20Hierarchical%20Modeling/chap10-historical_data.csv")

print(call_df.info())
print("...... ")
print(call_df.head())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 695205 entries, 0 to 695204
Data columns (total 7 columns):
 #   Column     Non-Null Count   Dtype  
---  ------     --------------   -----  
 0   center_ID  695205 non-null  int64  
 1   rep_ID     695205 non-null  int64  
 2   age        695205 non-null  int64  
 3   reason     695205 non-null  object 
 4   month      695205 non-null  int64  
 5   call_CSAT  695205 non-null  float64
 6   M6Spend    695205 non-null  float64
dtypes: float64(2), int64(4), object(1)
memory usage: 37.1+ MB
None
...... 
   center_ID  rep_ID  age   reason  month  call_CSAT     M6Spend
0          1       1   45  payment      3   5.837943    0.000000
1          1       1   21  payment      3   5.200015  115.834946
2          1       1   30  payment      3   4.397971   31.255470
3          1       1   51  payment      1   5.337387    0.000000
4          1       1   60  payment      3   5.463705    0.000000


### Introductory Look at the Data

We have 10 Call Centers with 15 - 22 representatives each

In [49]:
call_df.groupby('center_ID')['rep_ID'].nunique()

center_ID
1     18
2     21
3     22
4     15
5     21
6     21
7     19
8     19
9     19
10    18
Name: rep_ID, dtype: int64

Here we can see that the call center and representative are perfectly correlated

In [57]:
fig  = px.imshow(call_df.corr(), 
                text_auto=True,
                color_continuous_scale = 'viridis', 
                title = 'Correlation Matrix for Call Center Data')
fig.update_layout(height = 500, width = 1000) 
fig.show()
call_df.corr()

center_ID    rep_ID       age     month  call_CSAT   M6Spend
center_ID   1.000000  0.994726  0.001041 -0.000623   0.354594  0.027474
rep_ID      0.994726  1.000000  0.000951 -0.000213   0.353302  0.027327
age         0.001041  0.000951  1.000000 -0.000858   0.163388 -0.280797
month      -0.000623 -0.000213 -0.000858  1.000000  -0.000185  0.000838
call_CSAT   0.354594  0.353302  0.163388 -0.000185   1.000000  0.058590
M6Spend     0.027474  0.027327 -0.280797  0.000838   0.058590  1.000000

When modelling we kno

In [67]:
mixed1 = smf.mixedlm("call_CSAT ~ reason + age", 
                    data = call_df, 
                    groups = call_df['center_ID'])
mixed1.fit().summary()

<class 'statsmodels.iolib.summary2.Summary'>
"""
            Mixed Linear Model Regression Results
=============================================================
Model:              MixedLM Dependent Variable: call_CSAT    
No. Observations:   695205  Method:             REML         
No. Groups:         10      Scale:              1.1217       
Min. group size:    54203   Log-Likelihood:     -1026427.7247
Max. group size:    79250   Converged:          Yes          
Mean group size:    69520.5                                  
-------------------------------------------------------------
                   Coef. Std.Err.    z    P>|z| [0.025 0.975]
-------------------------------------------------------------
Intercept          3.899    0.335  11.641 0.000  3.243  4.556
reason[T.property] 0.199    0.003  74.786 0.000  0.194  0.205
age                0.020    0.000 176.747 0.000  0.020  0.020
Group Var          1.122    0.407                            
=============================================================

"""

In [66]:
vcf = {'rep_ID':'0+C(rep_ID)'}
mixed2 = smf.mixedlm("call_CSAT ~ reason + age", 
                    data = call_df, 
                    groups = call_df['center_ID'], 
                    vc_formula= vcf)
mixed2.fit().summary()

<class 'statsmodels.iolib.summary2.Summary'>
"""
            Mixed Linear Model Regression Results
=============================================================
Model:             MixedLM  Dependent Variable:  call_CSAT   
No. Observations:  695205   Method:              REML        
No. Groups:        10       Scale:               0.3904      
Min. group size:   54203    Log-Likelihood:      -660498.6462
Max. group size:   79250    Converged:           Yes         
Mean group size:   69520.5                                   
-------------------------------------------------------------
                   Coef. Std.Err.    z    P>|z| [0.025 0.975]
-------------------------------------------------------------
Intercept          3.874    0.099  38.992 0.000  3.679  4.069
reason[T.property] 0.200    0.002 126.789 0.000  0.196  0.203
age                0.020    0.000 298.301 0.000  0.020  0.020
rep_ID Var         1.904    0.303                            
=============================================================

"""